In [106]:
import pandas as pd
import os
import numpy as np
import altair as alt
import panel as pn
from vega_datasets import data
alt.data_transformers.enable('vegafusion')

DataTransformerRegistry.enable('vegafusion')

### Explore data sets

In [ ]:
folder_path = "../data"
filename = "aggregates_correspondence_table_2020_1.xlsx"
file_path = os.path.join(folder_path, filename)
correspondence = pd.read_excel(file_path, sheet_name="Annex", skiprows=10, header=0)
correspondence = correspondence.iloc[:, 1:]

In [ ]:
filename = "undesa_pd_2015_migration_flow_totals.xlsx"
file_path = os.path.join(folder_path, filename)
total_flow = pd.read_excel(file_path, sheet_name="Totals", skiprows=16, header=0)

In [ ]:
filename = "undesa_pd_2020_ims_stock_by_age_sex_and_destination.xlsx"
file_path = os.path.join(folder_path, filename)
stock_destination = pd.read_excel(file_path, sheet_name="Totals", skiprows=16, header=0)

In [ ]:
filename = "undesa_pd_2020_ims_stock_by_sex_destination_and_origin.xlsx"
file_path = os.path.join(folder_path, filename)
total_stock = pd.read_excel(file_path, sheet_name="Table 1", skiprows=10, header=0)
total_stock=total_stock.iloc[:, 1:]

In [52]:
total_stock = pd.read_excel("../data/undesa_pd_2020_ims_stock_by_sex_destination_and_origin.xlsx", 
                                sheet_name="Table 1", skiprows=10, header=0)
total_stock=total_stock.iloc[:, 1:]

### Main data

In [ ]:
def clean_total_stock():
    #Data frame
    total_stock = pd.read_excel("../data/undesa_pd_2020_ims_stock_by_sex_destination_and_origin.xlsx", 
                                sheet_name="Table 1", skiprows=10, header=0)
    total_stock=total_stock.iloc[:, 1:]

    # Correctly name missing values
    total_stock.replace('..', np.nan, inplace=True)

    #Rename columns
    total_stock.rename(columns={"Region, development group, country or area of destination":"Destination",
                                "Location code of destination":"Destination code",
                                "Region, development group, country or area of origin": "Origin",
                                "Location code of origin":"Origin code"}, inplace =True)

    #Keep only countries for destination and origin (original data frame has aggregations)
    countries = pd.read_csv("../data/country-coord.csv")
    #1. Destination
    total_stock['M1']=total_stock["Destination code"].isin(countries["Numeric code"])
    #2. Origin
    total_stock['M2']=total_stock["Origin code"].isin(countries["Numeric code"]) | (total_stock['Origin code'] == 2003)
    #3. Keep only if both are countries
    total_stock = total_stock[total_stock['M1'] & total_stock['M2']].copy()
    
    #Keep only neccesary columns
    total_stock = total_stock[["Destination","Destination code","Origin",
                               "Origin code",1990,1995,2000,2005,2010,2015,2020]]
    
    #Transform from wide to long
    year_columns = [1990, 1995, 2000, 2005, 2010, 2015, 2020]
    total_stock = pd.melt(total_stock,
                          id_vars=[col for col in total_stock.columns if col not in year_columns],
                          value_vars=year_columns,
                          var_name='Year',
                          value_name='Migration')

    # Change Value column to numeric
    total_stock['Migration'] = pd.to_numeric(total_stock['Migration'], errors='coerce')

    return total_stock

In [38]:
total_stock = total_stock[total_stock['Year'] == 2020]

In [ ]:
def other_total():
    total_stock = clean_total_stock()
    year_columns = [1990, 1995, 2000, 2005, 2010, 2015, 2020]
    total_grouped = total_stock.groupby("Destination")[year_columns].sum().reset_index()
    other_grouped = total_stock[total_stock['Origin code'] == 2003].groupby("Destination")[year_columns].sum().reset_index()
    results = total_grouped.merge(other_grouped, on="Destination", how="left", suffixes=("_Total", "_Other"))
    for year in year_columns:
        results[f"{year}_Other"] = results[f"{year}_Other"].fillna(0)
    for year in year_columns:
        results[f"{year}_Percentage_Other"] = (
            results[f"{year}_Other"] / results[f"{year}_Total"]
        ) * 100
    output_columns = ["Destination"] + [
        col for year in year_columns for col in [f"{year}_Total", f"{year}_Other", f"{year}_Percentage_Other"]
    ]
    results = results[output_columns]

    return results

In [49]:
def clean_estimates():
    # Data frame
    estimates = pd.read_excel("/Users/paulacadena/Git-Hub/CAPP30239-IP/data/WPP2024_GEN_F01_DEMOGRAPHIC_INDICATORS_COMPACT.xlsx", 
                                sheet_name="Estimates", skiprows=16, header=0)

    # Correctly name missing values
    estimates.replace('..', np.nan, inplace=True)

    # Keep only subregions
    subregion_codes = [1834,1833,1831,1832,1830,1835,1836,1829]
    estimates = estimates[estimates['Location code'].isin(subregion_codes)]
    
    # Keep only neccesary columns and rename them
    estimates = estimates[["Region, subregion, country or area *","Year","Net Migration Rate (per 1,000 population)"]]

    estimates.rename(
        columns={
            "Region, subregion, country or area *": "Subregion",
            "Net Migration Rate (per 1,000 population)": "Net Migration Rate"
        }, inplace=True
    )
    return estimates
estimates = clean_estimates()

In [57]:
def clean_region_stock():
    total_stock = pd.read_excel("../data/undesa_pd_2020_ims_stock_by_sex_destination_and_origin.xlsx", 
                                sheet_name="Table 1", skiprows=10, header=0)

    total_stock.replace('..', np.nan, inplace=True)

    total_stock.rename(columns={"Region, development group, country or area of destination":"Subregion",
                                    "Location code of destination":"Destination code",
                                    "Region, development group, country or area of origin": "source",
                                    "Location code of origin":"Origin code"}, inplace =True)
    subregion_codes = [947,921,927,1834,1833,1831,1832,1830,1835,1836,1829]
    region_stock = total_stock[total_stock['Destination code'].isin(subregion_codes) 
                               & total_stock['Origin code'].isin(subregion_codes)]
    region_stock = region_stock[["Subregion","source",1990,1995,2000,2005,
                                 2010,2015,2020]]
    year_columns = [1990, 1995, 2000, 2005, 2010, 2015, 2020]
    region_stock = pd.melt(region_stock,
                            id_vars=[col for col in region_stock.columns 
                                     if col not in year_columns],
                            value_vars=year_columns,
                            var_name='Year',
                            value_name='value')
    region_stock['Subregion'] = region_stock['Subregion'].str.strip()

    region_stock['Subregion'] = region_stock['Subregion'].replace({'Australia and New Zealand': 'Australia/New Zealand'})

    region_stock['value'] = pd.to_numeric(region_stock['value'], errors='coerce')
    return region_stock
region_stock = clean_region_stock()

In [122]:
def clean_sex_stock():
    total_stock = pd.read_excel("../data/undesa_pd_2020_ims_stock_by_sex_destination_and_origin.xlsx", 
                                sheet_name="Table 1", skiprows=10, header=0)

    total_stock.replace('..', np.nan, inplace=True)

    total_stock.rename(columns={"Region, development group, country or area of destination":"Destination",
                                    "Location code of destination":"Destination code",
                                    "Region, development group, country or area of origin": "Origin",
                                    "Location code of origin":"Origin code"}, inplace =True)
    #Keep only countries for destination and origin (original data frame has aggregations)
    countries = pd.read_csv("../data/country-coord.csv")
    #1. Destination
    total_stock['M1']=total_stock["Destination code"].isin(countries["Numeric code"])
    #2. Origin
    total_stock['M2']=total_stock["Origin code"].isin(countries["Numeric code"]) | (total_stock['Origin code'] == 2003)
    #3. Keep only if both are countries
    total_stock = total_stock[total_stock['M1'] & total_stock['M2']].copy()

    sex_stock = total_stock[["Destination","Destination code","Origin",
                               "Origin code","1990.1","1995.1","2000.1","2005.1",
                               "2010.1","2015.1","2020.1","1990.2","1995.2",
                               "2000.2","2005.2","2010.2","2015.2","2020.2"]]
    
    # Reshape the data into a long format, combining male and female columns
    sex_stock_long = pd.melt(
        sex_stock,
        id_vars=["Destination", "Destination code", "Origin", "Origin code"],
        var_name="Year_Sex",
        value_name="Migration"
    )

    # Extract year and sex from the 'Year_Sex' column
    sex_stock_long['Year'] = sex_stock_long['Year_Sex'].str[:-2].astype(int)
    sex_stock_long['Sex'] = sex_stock_long['Year_Sex'].str[-1]
    sex_stock_long['Sex'] = sex_stock_long['Sex'].replace({'1': 'Male', '2': 'Female'})

    # Drop the temporary 'Year_Sex' column
    sex_stock_long = sex_stock_long.drop('Year_Sex', axis=1)

    return sex_stock_long

sex_stock = clean_sex_stock()


### Visualizations

In [73]:
def migration_flow(selected_year=2020):
    total_stock = clean_total_stock()
    total_stock.drop(total_stock[total_stock['Origin code'] == 2003].index, inplace=True)

    countries = pd.read_csv("/Users/paulacadena/Git-Hub/CAPP30239-IP/data/country-coord.csv")
    countries.rename(columns={"Latitude (average)":"latitude", "Longitude (average)":"longitude"}, inplace=True)

    source = alt.topo_feature(data.world_110m.url, 'countries')

    select_country = alt.selection_point(
        on="pointerover", nearest=True, fields=["Destination code"], empty=False
    )

    lookup_data = alt.LookupData(
        countries, key="Numeric code", fields=["Country", "latitude", "longitude"]
    )

    total_stock_filtered = total_stock[total_stock['Year'] == selected_year]

    total_stock_aggregated = total_stock_filtered.groupby('Destination code', as_index=False).agg(
        Migrants=('Migration', 'sum')
    )

    background = alt.Chart(source).mark_geoshape(
        stroke="white"
    ).encode(
        color=alt.Color(
            'Migrants:Q',
            legend=alt.Legend(title='Total Immigrants')
        )
    ).transform_lookup(
        lookup="id",
        from_=alt.LookupData(total_stock_aggregated, key="Destination code", fields=["Migrants"])
    ).properties(
        width=800,
        height=500
    ).project('equalEarth')

    connections = alt.Chart(total_stock_filtered).mark_rule(opacity=0.1).encode(
        latitude="latitude:Q",
        longitude="longitude:Q",
        latitude2="lat2:Q",
        longitude2="lon2:Q"
    ).transform_lookup(
        lookup="Destination code",
        from_=lookup_data
    ).transform_lookup(
        lookup="Origin code",
        from_=lookup_data,
        as_=["Country", "lat2", "lon2"]
    ).transform_filter(
        select_country
    )

    points = alt.Chart(total_stock_filtered).mark_circle(size=0).encode(
        latitude="latitude:Q",
        longitude="longitude:Q",
        order=alt.Order("Immigrants:Q").sort("descending"),
        tooltip=[alt.Tooltip("Country:N"), alt.Tooltip("Immigrants:Q", format=",")]
    ).transform_aggregate(
        Immigrants="sum(Migration)",
        groupby=["Destination code"]
    ).transform_lookup(
        lookup="Destination code",
        from_=lookup_data
    ).add_params(
        select_country
    ).interactive()

    return (background + connections + points)
migration_flow()


alt.LayerChart(...)

In [ ]:
import altair as alt
import pandas as pd
import numpy as np

# Example DataFrame with gender distribution
data = pd.DataFrame({
    "id": range(1, 101),
    "gender": np.random.choice(["Male", "Female"], size=100, p=[0.5, 0.5])  # 60% Male, 40% Female
})

# Order the data by gender first (e.g., all Male first, then Female)
data = data.sort_values(by="gender", ascending=True).reset_index(drop=True)

# Calculate row and column for each point (10x10 grid)
data['row'] = np.ceil((data.index + 1) / 10).astype(int)
data['col'] = (data.index % 10) + 1

# Assign emojis based on gender
data['isotype'] = data['gender'].map({"Male": "🚹", "Female": "🚺"})

# Create chart with emojis
chart = alt.Chart(data).mark_text(
    align='center',
    baseline='middle',
    fontSize=40
).encode(
    alt.X("col:O").axis(None),
    alt.Y("row:O").axis(None),
    alt.Text("isotype:N"),
    tooltip=  [alt.Tooltip("gender:N")]
).properties(
    width=600,
    height=600
).configure_view(
    strokeWidth=0
)

chart

alt.Chart(...)

In [153]:
def migration_flow(selected_year=2020):
    total_stock = clean_total_stock()
    total_stock.drop(total_stock[total_stock['Origin code'] == 2003].index, inplace=True)
    sex_stock = clean_sex_stock()

    countries = pd.read_csv("/Users/paulacadena/Git-Hub/CAPP30239-IP/data/country-coord.csv")
    countries.rename(columns={"Latitude (average)":"latitude", "Longitude (average)":"longitude"}, inplace=True)

    source = alt.topo_feature(data.world_110m.url, 'countries')

    select_country = alt.selection_point(
        on="pointerover", nearest=True, fields=["Destination code"], empty=False
    )

    lookup_data = alt.LookupData(
        countries, key="Numeric code", fields=["Country", "latitude", "longitude"]
    )

    total_stock_filtered = total_stock[total_stock['Year'] == selected_year]
    sex_stock_filtered = sex_stock[sex_stock['Year']==selected_year]

    total_stock_aggregated = total_stock_filtered.groupby('Destination code', as_index=False).agg(
        Migrants=('Migration', 'sum')
    )

    background = alt.Chart(source).mark_geoshape(
        stroke="white"
    ).encode(
        color=alt.Color(
            'Migrants:Q',
            legend=alt.Legend(title='Total Immigrants')
        )
    ).transform_lookup(
        lookup="id",
        from_=alt.LookupData(total_stock_aggregated, key="Destination code", fields=["Migrants"])
    ).properties(
        width=700,
        height=400
    ).project('equalEarth')

    connections = alt.Chart(total_stock_filtered).mark_rule(opacity=0.1).encode(
        latitude="latitude:Q",
        longitude="longitude:Q",
        latitude2="lat2:Q",
        longitude2="lon2:Q"
    ).transform_lookup(
        lookup="Destination code",
        from_=lookup_data
    ).transform_lookup(
        lookup="Origin code",
        from_=lookup_data,
        as_=["Country", "lat2", "lon2"]
    ).transform_filter(
        select_country
    )

    points = alt.Chart(total_stock_filtered).mark_circle(size=0).encode(
        latitude="latitude:Q",
        longitude="longitude:Q",
        order=alt.Order("Immigrants:Q").sort("descending"),
        tooltip=[alt.Tooltip("Country:N"), alt.Tooltip("Immigrants:Q", format=",")]
    ).transform_aggregate(
        Immigrants="sum(Migration)",
        groupby=["Destination code"]
    ).transform_lookup(
        lookup="Destination code",
        from_=lookup_data
    ).add_params(
        select_country
    ).interactive()

    top_countries = total_stock_filtered.groupby(['Origin code', 'Destination code']).agg(
        Immigrants=('Migration', 'sum')
    ).reset_index()

    top_countries_aggregated = top_countries.groupby('Destination code').apply(
        lambda x: x.nlargest(5, 'Immigrants')
    ).reset_index(drop=True)

    top_countries_aggregated = top_countries_aggregated.merge(
        countries[['Numeric code', 'Country']], 
        left_on='Origin code', 
        right_on='Numeric code', 
        how='left'
    )

    bars = alt.Chart(top_countries_aggregated).mark_bar().encode(
        x=alt.X('Immigrants:Q', title='Total Immigrants'),
        y=alt.Y('Country:N', title='Origin Country'),
        color=alt.Color('Country:N',legend=None),
        tooltip=[alt.Tooltip('Country:N'), alt.Tooltip('Immigrants:Q', format=",")]
    ).transform_filter(
        select_country
    ).properties(
        width=150,
        height=150
    )

    pie = alt.Chart(sex_stock_filtered).mark_arc().encode(
        theta=alt.Theta("sum(Migration):Q",stack="normalize"),
        color="Sex"
        ).transform_filter(
        select_country
        ).properties(
        width=150,
        height=150,
        title = "Sex Distribution"
    )
    
    detail = alt.vconcat(bars, pie)

    return (background + connections + points | detail)

migration_flow()

/var/folders/mj/plt9jbg16hs2fg3v90d2csx80000gn/T/ipykernel_17572/1068312907.py:76: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



alt.HConcatChart(...)

In [145]:
sex_stock = clean_sex_stock()
base = alt.Chart(sex_stock).mark_arc().encode(
        theta=alt.Theta("sum(Migration):Q",stack="normalize"),
        color="Sex"
        )
pie = base.mark_arc(outerRadius=120)
# text = base.mark_text(radius=140, size=10).encode(
#     text=alt.Text("Percentage:Q", stack="normalize")
# )
# pie + text

pie

alt.Chart(...)